Gares et stations du réseau ferré d'Île-de-France (par ligne)<br>
https://data.iledefrance-mobilites.fr/explore/dataset/emplacement-des-gares-idf/information/?location=16,48.85089,2.51991&basemap=jawg.streets

In [1]:
import pandas as pd
import numpy as np
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
# pd.set_option('display.float_format', lambda x: '%.1f' % x)
import datetime
import math

import geopandas as gpd
from shapely.geometry import Point
from shapely.geometry.polygon import Polygon
from branca.element import Template, MacroElement
import branca.colormap as cm
import folium
from folium import plugins

In [2]:
idf_transport_geo = pd.read_json('data/ligne-transport.geojson')
idf_station_df = pd.read_csv('data/emplacement-des-gares-idf.csv', sep=';', decimal='.')

In [3]:
idf_station_df.head(2)

Geo Point  \
0  48.8794817719,2.38911580738   
1  48.8607869635,2.32099819195   

                                           Geo Shape  OBJECTID  id_ref_zdl  \
0  {"type": "Point", "coordinates": [2.3891158073...         3       42369   
1  {"type": "Point", "coordinates": [2.3209981919...        27       45704   

   gares_id             nom_gare              nomlong               nom_iv  \
0        93             Botzaris             BOTZARIS             Botzaris   
1        30  Assemblée Nationale  ASSEMBLEE NATIONALE  Assemblée Nationale   

   num_mod  mode_  fer  train  rer  metro  tramway  navette  val terfer  \
0     2362  Metro    0      0    0      1        0        0    0      0   
1     2312  Metro    0      0    0      1        0        0    0      0   

  tertrain terrer termetro tertram ternavette terval idrefliga idrefligc  \
0        0      0        0       0          0      0    A01550       NaN   
1        0      0        0       0          0      0    A01545       NaN   

  ligne  cod_ligf ligne_code indice_lig reseau res_com  cod_resf  res_stif  \
0    7b      14.0  7b-117033         7b  METRO   M7bis       3.0     110.0   
1    12       4.0  12-112059         12  METRO     M12       3.0     110.0   

  exploitant  num_psr  idf  principal            x             y  \
0       RATP        0    1          0  655197.2716  6.864558e+06   
1       RATP        0    1          0  650183.7135  6.862520e+06   

                                         picto ligne  
0  https://data.iledefrance-mobilites.fr/api/v2/c...  
1  https://data.iledefrance-mobilites.fr/api/v2/c...

In [4]:
idf_station_df['lat'], idf_station_df['lng'] = zip(*idf_station_df['Geo Point'].apply(lambda x: x.split(',')))
idf_station_df['lat'] = idf_station_df['lat'].astype(float)
idf_station_df['lng'] = idf_station_df['lng'].astype(float)
idf_station_df = idf_station_df[idf_station_df['mode_'].isin(['Metro', 'RER'])]

In [5]:
idf_map = folium.Map(location=[48.868, 2.365], zoom_start=12, tiles='cartodbpositron')
for line_segment in idf_transport_geo['features']:
    gjson = folium.features.GeoJson(line_segment['geometry'],
                                    style_function = lambda x: {'color': '#00C4B3', 'weight': 1.5})
    idf_map.add_child(gjson)

for i, v in idf_station_df.iterrows():
    folium.CircleMarker(location=[v['lat'], v['lng']],
                        radius=1.2,
                        color='#00C4B3',
                        fill_color='#00C4B3',
                        fill=True).add_to(idf_map)

idf_map#.save('m.html')